# ガウス過程

PHYSBOではガウス過程回帰を実行しながらベイズ最適化を行なっています。

そのため、学習データが与えられた際にガウス過程回帰を実行することもでき、学習済みモデルを利用したテストデータの予測も行うことができます。

ここでは、その手順について紹介します。


## 探索候補データの準備

これまでのマニュアルでも利用していたs5-210.csvを用いてガウス過程を実行します。

In [1]:
import physbo

import numpy as np

def load_data():
    A =  np.asarray(np.loadtxt('data/s5-210.csv',skiprows=1, delimiter=',') )
    X = A[:,0:3]
    t  = -A[:,3]
    return X, t

X, t = load_data()
X = physbo.misc.centering( X )


## 学習データの定義

対象データのうち、ランダムに選んだ1割をトレーニングデータとして利用し、別のランダムに選んだ1割をテストデータとして利用します。

In [2]:
N = len(t)
Ntrain = int(N*0.1)
Ntest = min(int(N*0.1), N-Ntrain)

id_all   = np.random.choice(N, N, replace=False)
id_train  = id_all[0:Ntrain]
id_test = id_all[Ntrain:Ntrain+Ntest]

X_train = X[id_train]
X_test = X[id_test]

t_train = t[id_train]
t_test = t[id_test]

print("Ntrain =", Ntrain)
print("Ntest =", Ntest)

Ntrain = 1798
Ntest = 1798


## ガウス過程の学習と予測

以下のプロセスでガウス過程を学習し、テストデータの予測を行います。

1. ガウス過程のモデルを生成します。

2. X_train（学習データのパラメータ）, t_train（学習データの目的関数値）を用いてモデルを学習します。

3. 学習されたモデルを用いてテストデータ(X_test)に対する予測を実行します。

共分散の定義(ガウシアン)

In [3]:
cov = physbo.gp.cov.gauss( X_train.shape[1],ard = False )

平均の定義

In [4]:
mean = physbo.gp.mean.const()

尤度関数の定義(ガウシアン)

In [5]:
lik = physbo.gp.lik.gauss()

ガウス過程モデルの生成

In [6]:
gp = physbo.gp.model(lik=lik,mean=mean,cov=cov)
config = physbo.misc.set_config()

ガウス過程モデルを学習

In [7]:
gp.fit(X_train, t_train, config)

Start the initial hyper parameter searching ...
Done

Start the hyper parameter learning ...
0 -th epoch marginal likelihood 17312.31220145003
50 -th epoch marginal likelihood 6291.292745798703
100 -th epoch marginal likelihood 3269.1167759139516
150 -th epoch marginal likelihood 1568.3930580794922
200 -th epoch marginal likelihood 664.2847129159145
250 -th epoch marginal likelihood -249.28468708456558
300 -th epoch marginal likelihood -869.7604930929888
350 -th epoch marginal likelihood -1316.6809532065581
400 -th epoch marginal likelihood -1546.1623851368954
450 -th epoch marginal likelihood -1660.7298135295766
500 -th epoch marginal likelihood -1719.5056128528097
Done



学習されたガウス過程におけるパラメタを出力

In [8]:
gp.print_params()



likelihood parameter =   [-2.81666924]
mean parameter in GP prior:  [-1.05939674]
covariance parameter in GP prior:  [-0.91578975 -2.45544347]




テストデータの平均値（予測値）および分散を計算

In [9]:
gp.prepare(X_train, t_train)
fmean = gp.get_post_fmean(X_train, X_test)
fcov = gp.get_post_fcov(X_train, X_test)

予測の結果

In [10]:
fmean

array([-1.00420815, -1.10923758, -0.97840623, ..., -1.00323733,
       -0.97015759, -1.11076236])

分散の結果

In [11]:
fcov

array([0.00056069, 0.00075529, 0.00043006, ..., 0.0016925 , 0.00070103,
       0.00073499])

予測値の平均二乗誤差の出力

In [12]:
np.mean((fmean-t_test)**2)

0.008107085662147708

## 訓練済みモデルによる予測

学習済みモデルのパラメタをgp_paramsとして読み出し、これを用いた予測を行います。

gp_paramsおよび学習データ(X_train, t_train)を記憶しておくことで、訓練済みモデルによる予測が可能となります。

学習されたパラメタを準備(学習の直後に行う必要あり)

In [13]:
#学習したパラメタを１次元配列として準備
gp_params =  np.append(np.append(gp.lik.params, gp.prior.mean.params), gp.prior.cov.params)

gp_params

array([-2.81666924, -1.05939674, -0.91578975, -2.45544347])

学習に利用したモデルと同様のモデルをgpとして準備

In [14]:
#共分散の定義 (ガウシアン)
cov = physbo.gp.cov.gauss( X_train.shape[1],ard = False )

#平均の定義
mean = physbo.gp.mean.const()

#尤度関数の定義 (ガウシアン)
lik = physbo.gp.lik.gauss()

#ガウス過程モデルの生成
gp = physbo.gp.model(lik=lik,mean=mean,cov=cov)


学習済みのパラメタをモデルに入力し予測を実行

In [15]:
#学習済みのパラメタをガウス過程に入力
gp.set_params(gp_params)


#テストデータの平均値（予測値）および分散を計算
gp.prepare(X_train, t_train)
fmean = gp.get_post_fmean(X_train, X_test)
fcov = gp.get_post_fcov(X_train, X_test)

予測の結果

In [16]:
fmean

array([-1.00420815, -1.10923758, -0.97840623, ..., -1.00323733,
       -0.97015759, -1.11076236])

分散の結果

In [17]:
fcov

array([0.00056069, 0.00075529, 0.00043006, ..., 0.0016925 , 0.00070103,
       0.00073499])

予測値の平均二乗誤差の出力

In [18]:
np.mean((fmean-t_test)**2)

0.008107085662147708